In [32]:
#!pip install huggingface_hub torch transformers datasets trl 
#!pip install flash-attn --no-build-isolation
!pip install --upgrade peft

In [35]:
import sys
import logging

import datasets
from datasets import load_dataset
from peft import LoraConfig
import torch
import torch.nn as nn
import transformers
from trl import SFTTrainer, SFTConfig
from transformers import AutoModelForCausalLM, AutoTokenizer, TrainingArguments, BitsAndBytesConfig

In [2]:
from huggingface_hub import HfApi, notebook_login

notebook_login()

In [3]:
api = HfApi()

quant_repo = "Granther/assorted-notebooks-bin"

api.upload_file(
    path_or_fileobj="sft_phi3_2.ipynb",
    path_in_repo="sft_phi3_2.ipynb",
    repo_id=quant_repo,
    repo_type="dataset",
)

CommitInfo(commit_url='https://huggingface.co/datasets/Granther/assorted-notebooks-bin/commit/daccf7107bc7eac6717dea879fde2ba3a51cccf4', commit_message='Upload sft_phi3_2.ipynb with huggingface_hub', commit_description='', oid='daccf7107bc7eac6717dea879fde2ba3a51cccf4', pr_url=None, pr_revision=None, pr_num=None)

In [4]:
dataset_id = ("wikitext", "wikitext-103-raw-v1")
dataset_id = "HuggingFaceH4/ultrachat_200k"

dataset = load_dataset(dataset_id)

In [5]:
training_config = {
    "bf16": True,
    "do_eval": False,
    "do_train": True, # defualts to False, not sure where this fits
    "learning_rate": 5.0e-06,
    "log_level": "info",
    "logging_steps": 20,
    "logging_strategy": "steps",
    "lr_scheduler_type": "cosine",
    "num_train_epochs": 1,
    "max_steps": -1,
    "output_dir": "./checkpoint_dir", # model predictions and checkpoints
    "overwrite_output_dir": True,
    "per_device_eval_batch_size": 4,
    "per_device_train_batch_size": 4,
    "remove_unused_columns": True,
    "save_steps": 100,
    "save_total_limit": 1,
    "seed": 0,
    "gradient_checkpointing": True,
    "gradient_checkpointing_kwargs":{"use_reentrant": False},
    "gradient_accumulation_steps": 1, # number of steps to accumulate before beckprop
    "warmup_ratio": 0.2,
    "packing": False,
    "max_seq_length": 2048,
    "dataset_text_field": "text",
    }

peft_config = {
    "r": 16, # default values VV
    "lora_alpha": 32,
    "lora_dropout": 0.05,
    "bias": "none",
    "task_type": "CAUSAL_LM",
    "target_modules": "all-linear",
    "modules_to_save": None,
}

train_conf = SFTConfig(**training_config)
#train_conf = TrainingArguments(**training_config)
peft_conf = LoraConfig(**peft_config)

In [6]:
checkpoint_path = "microsoft/Phi-3-mini-128k-instruct"
model_kwargs = dict(
    use_cache=False,
    trust_remote_code=True,
    attn_implementation="flash_attention_2",  # loading the model with flash-attenstion support
    torch_dtype=torch.bfloat16,
    device_map="auto"
)

model = AutoModelForCausalLM.from_pretrained(checkpoint_path, **model_kwargs)
tokenizer = AutoTokenizer.from_pretrained(checkpoint_path, truncation=True)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [6]:
tokenizer.model_max_length = 2048
#tokenizer.pad_token = tokenizer.unk_token  # use unk rather than eos token to prevent endless generation
#tokenizer.pad_token_id = tokenizer.convert_tokens_to_ids(tokenizer.pad_token)
tokenizer.padding_side = 'right'

In [7]:
def preproc(examples, tokenizer):
    messages = examples['messages']
    examples['text'] = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=False) #, return_dict=True)
    return examples

train_dataset = dataset['train_sft']
test_dataset = dataset['test_sft']

train_dataset = train_dataset.map(preproc,
                            fn_kwargs={'tokenizer':tokenizer},
                            num_proc=24,
                            #batched=True,
                            remove_columns=list(train_dataset.features)).select(range(1000))

test_dataset = test_dataset.map(preproc,
                            fn_kwargs={'tokenizer':tokenizer},
                            num_proc=24,
                            #batched=True,
                            remove_columns=list(test_dataset.features))#[10000:]

In [8]:
trainer = SFTTrainer(
    model=model,
    args=train_conf,
    peft_config=peft_conf,
    train_dataset=train_dataset,
    #eval_dataset=test_dataset,
    # max_seq_length=tokenizer.model_max_length,
    # dataset_text_field="text",
    tokenizer=tokenizer,
    # packing=True
)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Using auto half precision backend


In [ ]:
train_result = trainer.train()
metrics = train_result.metrics
trainer.save_state()

In [12]:
metrics

{'train_runtime': 506.2204,
 'train_samples_per_second': 1.975,
 'train_steps_per_second': 0.494,
 'total_flos': 4.041582948790272e+16,
 'train_loss': 1.1037534561157227,
 'epoch': 1.0}

In [7]:
from peft import PeftConfig, PeftModel 

checkpoint_path = "microsoft/Phi-3-mini-128k-instruct"
adapter_path = "./checkpoint_dir/checkpoint-250"

model_kwargs = dict(
    use_cache=False,
    trust_remote_code=True,
    attn_implementation="flash_attention_2",  # loading the model with flash-attenstion support
    torch_dtype=torch.bfloat16,
    device_map="auto"
)

model = AutoModelForCausalLM.from_pretrained(checkpoint_path, **model_kwargs)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [8]:
model = PeftModel.from_pretrained(model, adapter_path)
tokenizer = AutoTokenizer.from_pretrained(checkpoint_path)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [83]:
cats = None
kittens = None
paris = None

In [88]:
input_text = [
    {'role': 'user', 'content': "Cats are"},
    #{'role': 'system', 'content': "I'm going "}
]

input = "Tell me about paris"

input = tokenizer(input, return_tensors='pt')

def generate_out(input, len=100):
    return model.generate(
        input['input_ids'].to('cuda'),
        max_length=len,  # Maximum length of the generated text
        num_return_sequences=1,  # Number of sequences to generate
    )
output = generate_out(input)[0].to(torch.float32)

paris = output

#loss(output, output)
#input = tokenizer.apply_chat_template(input_text, tokenize=False, add_generation_prompt=False)


In [92]:
import numpy as np

np.exp(loss(cats, paris).item)

TypeError: loop of ufunc does not support argument 0 of type builtin_function_or_method which has no callable exp method

In [68]:
output[0]

tensor([  274,  1446,   526,   451,   278,   871, 15006,   393,   508,   367,
        15201,   491,   445,  4195, 29889,   360, 12099, 29892, 27127,  1169,
        29892,   322,  1584, 17952,   508,   884,  8812,   515,   445, 17135,
        29889,    13,    13,  1576, 25828,  4835,   310,   285,  5570,   454,
         2679, 29747, 24424,   297, 20309,   508, 13100,  8679,   373,   278,
         7408,   310,   278, 17135, 29889,   512,   278,  4688, 22950, 29892,
          274,  1446,  1122,  1510,   694, 18906,   310,  4486,  2264, 29889,
         2398, 29892,   408,   278, 17135,  6728,   267, 29892,   896,  1122,
         4953,   454,   386,  1191,   293, 29892, 14074,  1009,   623,   300,
          568, 29892,   322,  2693,  2381,   324,  2435,   301,   962,   561],
       device='cuda:0')

In [75]:
x = torch.tensor([123], dtype=torch.long)

#loss(x,x)

input = torch.randn(3, 5, requires_grad=True)
target = torch.empty(3, dtype=torch.long).random_(5)

target

tensor([4, 3, 0])

In [59]:
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print(generated_text)

cats are not the only animals that can be affected by this condition. Dogs, rabbits, and even birds can also suffer from this disease.

The symptoms of feline leukemia virus infection can vary depending on the stage of the disease. In the early stages, cats may show no signs of illness. However, as the disease progresses, they may become lethargic, lose their appetite, and develop swollen lymph


In [54]:
loss = nn.CrossEntropyLoss()

i = tokenizer("Hello", return_tensors='pt').to(torch.float16)
lab = tokenizer("Hella", return_tensors='pt').to(torch.float16

loss(generate_out(i,len=10), generate_out(lab,len=10))

#loss(i, lab)

                                    

Attempting to cast a BatchEncoding to type torch.float16. This is not supported.
Attempting to cast a BatchEncoding to type torch.float16. This is not supported.


RuntimeError: Expected floating point type for target with class probabilities, got Long

### Test perplexity using MMLU

In [ ]:
prompt = "When a diver points a flashlight upward toward the surface of the water at an angle 20° from the normal, the beam of light"
subject = "conceptual_physics"
answer = "passes into the air above"

input_text = []



In [1]:
!lm_eval --model hf \
    --model_args pretrained=EleutherAI/gpt-j-6B \
    --tasks hellaswag \
    --device cuda:0 \
    --batch_size 8

2024-07-04:16:55:06,590 INFO     [__main__.py:272] Verbosity set to INFO
2024-07-04:16:55:11,201 INFO     [__main__.py:369] Selected Tasks: ['hellaswag']
2024-07-04:16:55:11,202 INFO     [evaluator.py:152] Setting random seed to 0 | Setting numpy seed to 1234 | Setting torch manual seed to 1234
2024-07-04:16:55:11,202 INFO     [evaluator.py:189] Initializing hf model, with arguments: {'pretrained': 'EleutherAI/gpt-j-6B'}
2024-07-04:16:55:11,241 INFO     [huggingface.py:170] Using device 'cuda:0'
Generating test split: 100%|████| 10003/10003 [00:00<00:00, 17738.73 examples/s]
Generating validation split: 100%|█| 10042/10042 [00:00<00:00, 17489.21 examples
Map: 100%|███████████████████████| 10042/10042 [00:01<00:00, 9523.34 examples/s]
2024-07-04:16:56:20,566 INFO     [evaluator.py:261] Setting fewshot random generator seed to 1234
2024-07-04:16:56:20,567 INFO     [task.py:411] Building contexts for hellaswag on rank 0...
100%|███████████████████████████████████| 10042/10042 [00:02<00:00